In [1]:
%load_ext autoreload
%autoreload 2

In [1]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /content/drive/MyDrive/logical-reasoning/


In [17]:
need_to_setup_env = True

if need_to_setup_env:
    %pip install -r requirements.txt
    %cd /content/
    %rm -rf LLaMA-Factory
    !git clone https://github.com/hiyouga/LLaMA-Factory.git
    %cd LLaMA-Factory
    %ls
    %pip install -e .[torch,bitsandbytes]

    os.chdir(workding_dir)
    sys.path.append(workding_dir)
    print("workding dir:", workding_dir)

/content
Cloning into 'LLaMA-Factory'...
remote: Enumerating objects: 15796, done.
remote: Counting objects: 100% (6869/6869), done.
remote: Compressing objects: 100% (499/499), done.
remote: Total 15796 (delta 6499), reused 6416 (delta 6370), pack-reused 8927
Receiving objects: 100% (15796/15796), 222.26 MiB | 12.29 MiB/s, done.
Resolving deltas: 100% (11649/11649), done.
/content/LLaMA-Factory
assets/       docker/      LICENSE      pyproject.toml  requirements.txt  src/
CITATION.cff  evaluation/  Makefile     README.md       scripts/          tests/
data/         examples/    MANIFEST.in  README_zh.md    setup.py
Obtaining file:///content/LLaMA-Factory
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Preparing editable metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 245.8/245.8 kB 2.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 

In [3]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /content/drive/MyDrive/logical-reasoning/.env


True

In [4]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"
lora_repo_id = "inflaton-ai/InternLM_2_5-7b_LoRA-Adapter"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)
lora_repo_id

internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175 True datasets/mgtv results/mgtv-results_colab_p2.csv


'inflaton-ai/InternLM_2_5-7b_LoRA-Adapter'

In [7]:
%%time
!python --version
!pip show transformers torch torchvision torchaudio

Python 3.10.12
Name: transformers
Version: 4.41.2
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /usr/local/lib/python3.10/dist-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
Required-by: peft
---
Name: torch
Version: 2.3.1+cu121
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /usr/local/lib/python3.10/dist-packages
Requires: filelock, fsspec, jinja2, networkx, nvidia-cublas-cu12, nvidia-cuda-cupti-cu12, nvidia-cuda-nvrtc-cu12, nvidia-cuda-runtime-cu12, nvidia

In [6]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /content/drive/MyDrive/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
GPU is available


In [ ]:
%%time

model, tokenizer = load_model(adapter_name_or_path, using_llama_factory=False)

loading model: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175 with adapter: None


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


config.json:   0%|          | 0.00/895 [00:00<?, ?B/s]

configuration_internlm2.py:   0%|          | 0.00/8.84k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/internlm/internlm2_5-7b-chat-1m:
- configuration_internlm2.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


...

model-00007-of-00008.safetensors:   0%|          | 0.00/1.98G [00:00<?, ?B/s]

model-00008-of-00008.safetensors:   0%|          | 0.00/1.75G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/123 [00:00<?, ?B/s]

CPU times: user 29.2 s, sys: 23 s, total: 52.2 s
Wall time: 17min 39s


In [11]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [ ]:
print_row_details(datasets["test"].to_pandas(), [1000])

--------------------------------------------------
text: 哭泣和村庄有关系吗
--------------------------------------------------
label: 是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 甄庄哭声
--------------------------------------------------
puzzle: 在一个安静的夜晚，小村庄的湖边突然传来了阵阵哭泣声。第二天早晨，村长甄锐发现湖边的石头上放着一顶破旧的帽子，但没有人知道这顶帽子是从哪里来的，哭泣声又是为何。请还原故事真相。
--------------------------------------------------
truth: 原来，这顶破旧的帽子属于一个小男孩，他小时候与爷爷在湖边生活。爷爷教他钓鱼、游泳，还告诉他湖中的海龟是他们的朋友。后来，小男孩随父母去了城市生活，但每年夏天都会回到村子探望爷爷。然而，去年夏天，爷爷因病去世，小男孩伤心欲绝。今年夏天，他回到村子，来到湖边，想起和爷爷的美好回忆，忍不住哭泣。他将爷爷的帽子放在湖边的石头上，希望能让爷爷的在天之灵得到安慰。那晚的哭泣声正是小男孩在祭莫他亲爱的爷爷。
--------------------------------------------------
train_text: <s><|im_start|>system
You are an expert in logical reasoning.<|im_end|>
<|im_start|>user
你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是

In [ ]:
%%time

prompt1 = datasets["test"]["prompt"][1000]

gen_kwargs = {"max_length": 4096, "do_sample": True, "top_k": 1}
with torch.no_grad():
    inputs = tokenizer(
        [prompt1],
        return_tensors="pt",
    ).to(device)
    outputs = model.generate(**inputs, **gen_kwargs)
    outputs = outputs[:, inputs['input_ids'].shape[1]:]
    print(tokenizer.decode(outputs[0], skip_special_tokens=True))

是
CPU times: user 1.57 s, sys: 307 ms, total: 1.88 s
Wall time: 2.45 s


In [ ]:
model.push_to_hub(lora_repo_id)
tokenizer.push_to_hub(lora_repo_id)

README.md:   0%|          | 0.00/5.17k [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/integrations/peft.py:399: FutureWarning: The `active_adapter` method is deprecated and will be removed in a future version.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


adapter_model.safetensors:   0%|          | 0.00/37.8M [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/1.48M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/inflaton-ai/InternLM_2_5-7b_LoRA-Adapter/commit/d8c33cff42030f3c7c145c1df9bfbff17012c502', commit_message='Upload tokenizer', commit_description='', oid='d8c33cff42030f3c7c145c1df9bfbff17012c502', pr_url=None, pr_revision=None, pr_num=None)

In [ ]:
del model, tokenizer

In [ ]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path=lora_repo_id, using_llama_factory=False)

loading model: internlm/internlm2_5-7b-chat-1m with adapter: inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

CPU times: user 9.01 s, sys: 1.86 s, total: 10.9 s
Wall time: 13.6 s


In [ ]:
%%time

prompt1 = datasets["test"]["prompt"][1000]

gen_kwargs = {"max_length": 4096, "do_sample": True, "top_k": 1}
with torch.no_grad():
    inputs = tokenizer(
        [prompt1],
        return_tensors="pt",
    ).to(device)
    outputs = model.generate(**inputs, **gen_kwargs)
    outputs = outputs[:, inputs['input_ids'].shape[1]:]
    print(tokenizer.decode(outputs[0], skip_special_tokens=True))

是
CPU times: user 1.33 s, sys: 283 ms, total: 1.61 s
Wall time: 1.61 s


In [10]:
def evaluate_model(model, tokenizer, dataset, batch_size=8, load_in_4bit=False, using_llama_factory=False):
    save_model_name = f"{model_name}_{lora_repo_id}_l4_{model.dtype}{'_4bit' if load_in_4bit else ''}{'_lf' if using_llama_factory else ''}"
    print(f"Evaluating model: {save_model_name} on {device}")
    predictions = eval_model(
        model, tokenizer, dataset, device=device, batch_size=batch_size
    )

    save_results(
        save_model_name,
        results_path,
        dataset,
        predictions,
        debug=False,
    )

    metrics = calc_metrics(dataset["label"], predictions, debug=False)
    print(metrics)

In [ ]:
%%time

evaluate_model(model, tokenizer, datasets["test"])

Evaluating model: internlm/internlm2_5-7b-chat-1m_llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175_l4_torch.bfloat16 on cuda


  0%|          | 1/375 [00:03<22:56,  3.68s/it]

Batch output: ['不是', '是', '是', '是', '不是', '是', '是', '不是']


100%|██████████| 375/375 [24:02<00:00,  3.85s/it]


{'accuracy': 0.8106666666666666}
CPU times: user 24min 8s, sys: 1.63 s, total: 24min 10s
Wall time: 24min 3s


In [ ]:
del model, tokenizer

In [9]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path=lora_repo_id, dtype=torch.float16, using_llama_factory=False)
model.dtype, model.get_memory_footprint()

loading model: internlm/internlm2_5-7b-chat-1m with adapter: inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


tokenizer_config.json:   0%|          | 0.00/2.51k [00:00<?, ?B/s]

tokenization_internlm2_fast.py:   0%|          | 0.00/7.80k [00:00<?, ?B/s]

tokenization_internlm2.py:   0%|          | 0.00/8.81k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/internlm/internlm2_5-7b-chat-1m:
- tokenization_internlm2.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
A new version of the following files was downloaded from https://huggingface.co/internlm/internlm2_5-7b-chat-1m:
- tokenization_internlm2_fast.py
- tokenization_internlm2.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


...

generation_config.json:   0%|          | 0.00/123 [00:00<?, ?B/s]

adapter_config.json:   0%|          | 0.00/679 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/37.8M [00:00<?, ?B/s]

CPU times: user 52.5 s, sys: 34.5 s, total: 1min 27s
Wall time: 25min 16s


(torch.float16, 15513174016)

In [14]:
%%time

evaluate_model(model, tokenizer, datasets["test"])

Evaluating model: internlm/internlm2_5-7b-chat-1m_inflaton-ai/InternLM_2_5-7b_LoRA-Adapter_l4_torch.float16 on cuda


  0%|          | 1/375 [00:05<32:05,  5.15s/it]

Batch output: ['不是', '是', '是', '是', '不是', '是', '是', '不是']


100%|██████████| 375/375 [23:52<00:00,  3.82s/it]


{'accuracy': 0.8003333333333333}
CPU times: user 24min, sys: 253 ms, total: 24min 1s
Wall time: 23min 53s


In [15]:
del model, tokenizer

In [7]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path=lora_repo_id, dtype=torch.bfloat16, using_llama_factory=True)
model.dtype, model.get_memory_footprint()

loading model: internlm/internlm2_5-7b-chat-1m with adapter: inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:15:05,651 >> loading file ./tokenizer.model from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/./tokenizer.model
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:15:05,652 >> loading file added_tokens.json from cache at None
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:15:05,653 >> loading file special_tokens_map.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/special_tokens_map.json
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:15:05,654 >> loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/tokenizer_config.json
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:15:05,655 >> loading file tokenizer.json from cache at None


07/22/2024 14:15:06 - INFO - llamafactory.data.template - Add <|im_end|> to stop words.


INFO:llamafactory.data.template:Add <|im_end|> to stop words.
/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
[INFO|configuration_utils.py:733] 2024-07-22 14:15:07,004 >> loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/config.json
[INFO|configuration_utils.py:733] 2024-07-22 14:15:07,512 >> loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/config.json
[INFO|configuration_utils.py:796] 2024-07-22 14:15:07,514 >> Model config InternLM2Config {
  "_name_or_path": "internlm/internlm2_5-7b-chat-1m",
  "architectur

07/22/2024 14:15:07 - INFO - llamafactory.model.patcher - Using KV cache for faster generation.


...

INFO:llamafactory.model.adapter:Loaded adapter(s): inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


07/22/2024 14:15:18 - INFO - llamafactory.model.loader - all params: 7,737,708,544


INFO:llamafactory.model.loader:all params: 7,737,708,544


CPU times: user 16.7 s, sys: 2.75 s, total: 19.5 s
Wall time: 21.9 s


(torch.bfloat16, 15475425280)

In [11]:
%%time

evaluate_model(model, tokenizer, datasets["test"], using_llama_factory=True)

Evaluating model: internlm/internlm2_5-7b-chat-1m_inflaton-ai/InternLM_2_5-7b_LoRA-Adapter_l4_torch.bfloat16_lf on cuda


  0%|          | 1/375 [00:04<25:48,  4.14s/it]

Batch output: ['不是', '是', '是', '是', '不是', '是', '是', '不是']


100%|██████████| 375/375 [21:09<00:00,  3.39s/it]

{'accuracy': 0.8103333333333333}
CPU times: user 21min 16s, sys: 2.07 s, total: 21min 18s
Wall time: 21min 9s


In [19]:
del model, tokenizer

In [20]:
import gc
gc.collect()
torch.cuda.empty_cache()

In [7]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path=lora_repo_id, dtype=torch.float16, using_llama_factory=True)
model.dtype, model.get_memory_footprint()

loading model: internlm/internlm2_5-7b-chat-1m with adapter: inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:48:40,859 >> loading file ./tokenizer.model from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/./tokenizer.model
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:48:40,861 >> loading file added_tokens.json from cache at None
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:48:40,862 >> loading file special_tokens_map.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/special_tokens_map.json
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:48:40,863 >> loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/tokenizer_config.json
[INFO|tokenization_utils_base.py:2108] 2024-07-22 14:48:40,865 >> loading file tokenizer.json from cache at None


07/22/2024 14:48:41 - INFO - llamafactory.data.template - Add <|im_end|> to stop words.


INFO:llamafactory.data.template:Add <|im_end|> to stop words.
/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
[INFO|configuration_utils.py:733] 2024-07-22 14:48:42,978 >> loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/config.json
[INFO|configuration_utils.py:733] 2024-07-22 14:48:45,358 >> loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/config.json
[INFO|configuration_utils.py:796] 2024-07-22 14:48:45,361 >> Model config InternLM2Config {
  "_name_or_path": "internlm/internlm2_5-7b-chat-1m",
  "architectur

07/22/2024 14:48:45 - INFO - llamafactory.model.patcher - Using KV cache for faster generation.


...

INFO:llamafactory.model.adapter:Loaded adapter(s): inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


07/22/2024 14:49:01 - INFO - llamafactory.model.loader - all params: 7,737,708,544


INFO:llamafactory.model.loader:all params: 7,737,708,544


CPU times: user 17.5 s, sys: 1.81 s, total: 19.3 s
Wall time: 32.3 s


(torch.bfloat16, 15475425280)

In [12]:
%%time

evaluate_model(model, tokenizer, datasets["test"], using_llama_factory=True)

Evaluating model: internlm/internlm2_5-7b-chat-1m_inflaton-ai/InternLM_2_5-7b_LoRA-Adapter_l4_torch.bfloat16_lf on cuda


  0%|          | 1/375 [00:04<25:51,  4.15s/it]

Batch output: ['不是', '是', '是', '是', '不是', '是', '是', '不是']


100%|██████████| 375/375 [21:09<00:00,  3.39s/it]

{'accuracy': 0.8103333333333333}
CPU times: user 21min 16s, sys: 1.87 s, total: 21min 18s
Wall time: 21min 10s
